# Title  : Hausing Rental Analysis and Prediction in Delhi
Problem Statement



Requirement Analysis
1. Dataset : https://www.kaggle.com/datasets/goelyash/housing-price-dataset-of-delhiindia/data
2. Framework : Python + Scikit-learn(ML) + Pandas(Preprocessing) + matplotlib, seaborn(visualization)
3.

### Task-0 : Setup the developement enviroment

In [3]:
import pandas as pd

In [8]:
delhi = pd.read_csv('dataset/hausing-data-delhi_v2.csv')

print(delhi.describe())
delhi.head()

        Unnamed: 0         price         area     latitude    longitude  \
count  7738.000000  7.738000e+03  7738.000000  7738.000000  7738.000000   
mean   3868.500000  8.320635e+06  1409.506591    28.552092    77.273476   
std    2233.912524  7.223197e+06   718.929581     0.107420     0.180606   
min       0.000000  1.700000e+06   501.000000    28.240023    76.884101   
25%    1934.250000  4.200000e+06   990.000000    28.455539    77.078590   
50%    3868.500000  6.000000e+06  1250.000000    28.574637    77.345320   
75%    5802.750000  9.500000e+06  1650.000000    28.642520    77.421054   
max    7737.000000  8.500000e+07  9500.000000    28.799748    77.688028   

          Bedrooms    Bathrooms      Balcony      parking         Lift  \
count  7738.000000  7738.000000  5166.000000  2612.000000  1733.000000   
mean      2.708193     2.501163     2.426442     7.673047     1.829198   
std       0.877026     0.867050     1.083677    60.417508     1.192607   
min       2.000000     2.000

Unnamed: 0       price                                            Address  \
0           0   5600000.0                  Noida Extension, Noida, Delhi NCR   
1           1   8800000.0                      Sector 79, Gurgaon, Delhi NCR   
2           2  16500000.0                     Vaishali, Ghaziabad, Delhi NCR   
3           3   3810000.0  Link Road, F Block, Sector 50, Noida, Uttar Pr...   
4           4   6200000.0  Jaypee Pavilion Court Sector 128, Noida, Secto...   

     area   latitude  longitude  Bedrooms  Bathrooms  Balcony  \
0  1350.0  28.608850  77.460560       3.0        3.0      NaN   
1  1490.0  28.374236  76.952416       3.0        3.0      NaN   
2  2385.0  28.645769  77.385110       4.0        5.0      NaN   
3  1050.0  28.566914  77.436434       2.0        2.0      3.0   
4  1350.0  28.520732  77.356491       2.0        2.0      3.0   

               Status      neworold  parking Furnished_status  Lift  \
0  Under Construction  New Property      NaN              NaN   2.0   
1       Ready to Move  New Property      NaN   Semi-Furnished   2.0   
2       Ready to Move  New Property      1.0      Unfurnished   NaN   
3                 NaN  New Property      1.0      Unfurnished   2.0   
4       Ready to Move        Resale      1.0              NaN   3.0   

                    Landmarks type_of_building  \
0                         NaN             Flat   
1                         NaN             Flat   
2                         NaN             Flat   
3  near Gaur Mulberry Mansion             Flat   
4                         NaN             Flat   

                                                desc   Price_sqft  
0  \n\n\n                                Welcome ...  4148.148148  
1  \n\n\n                                Mapsko M...  5906.040268  
2  \n\n\n                                This pro...  6918.238994  
3  \n\n\n                                AIG Roya...  3628.571429  
4  \n\n\n                                The prop...  4592.592593

In [9]:
# make a copy of data
data = delhi

# drop the unamed column
data.drop(columns=['Unnamed: 0'], inplace=True)

# let's see the data types
print(data.dtypes)

# let's count all the object data types

for i in data.columns[data.dtypes=='object']:
    print(i, data[i].unique())
    print("\n")
    print(delhi[i].value_counts())


price               float64
Address              object
area                float64
latitude            float64
longitude           float64
Bedrooms            float64
Bathrooms           float64
Balcony             float64
Status               object
neworold             object
parking             float64
Furnished_status     object
Lift                float64
Landmarks            object
type_of_building     object
desc                 object
Price_sqft          float64
dtype: object
Address ['Noida Extension, Noida, Delhi NCR' 'Sector 79, Gurgaon, Delhi NCR'
 'Vaishali, Ghaziabad, Delhi NCR' ...
 'Sector137 Noida Paramount Floraville, Sector 137, Noida, Delhi NCR'
 'Greater Noida, Sector 2, Greater Noida, Delhi NCR'
 'sandal apartment, Shalimar Garden Extension 1, Ghaziabad, Delhi NCR']


Address
Raj Nagar Extension, Ghaziabad, Delhi NCR                                     163
Indirapuram, Ghaziabad, Delhi NCR                                             152
Greater Noida West, Greate

In [26]:
data1 = data
import numpy as np
import seaborn as sns
import folium
from folium.plugins import MarkerCluster

In [14]:
def editing(data):
    l=[]
    #data["District"]=[((i.split(","))[-2].lower()).strip() for i in data.Address]
    data=data[data.Price_sqft<75000]
    data.drop(columns=["Address","Status","desc","Price_sqft"],inplace=True)
    data.neworold.replace(["Resale","New Property",'Other\n\t\t\t\t\t\t\t\t\tGet Documents Verified'],[0,1,0],inplace=True)
    data.type_of_building.replace(["Flat","Individual House"],[0,1],inplace=True)
    data.Furnished_status.replace(['Semi-Furnished', 'Unfurnished', 'Furnished'],[1,0,2],inplace=True)
    for i in data.Landmarks:
        if type(i)==str:
            l.append(1)
        else:
            l.append(0)     
    data.Landmarks=l
    data.replace(np.nan,0,inplace=True)
    l=[]
    for i in data.Lift:
        if i>0:
            l.append(1)
        else:
            l.append(0)
    data.Lift=l
    l=[]        
    for i in data.parking:
        if i>0:
            l.append(1)
        else:
            l.append(0)        
    data.parking=l
    data.price=data.price/1000000
    data=data[data.price<100]
    data=data[data.price>1]
    return data  
data2=editing(data1)
data2.head()

/tmp/ipykernel_16127/2241693228.py:6: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  data.neworold.replace(["Resale","New Property",'Other\n\t\t\t\t\t\t\t\t\tGet Documents Verified'],[0,1,0],inplace=True)
/tmp/ipykernel_16127/2241693228.py:6: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  data.neworol

price    area   latitude  longitude  Bedrooms  Bathrooms  Balcony  \
0   5.60  1350.0  28.608850  77.460560       3.0        3.0      0.0   
1   8.80  1490.0  28.374236  76.952416       3.0        3.0      0.0   
2  16.50  2385.0  28.645769  77.385110       4.0        5.0      0.0   
3   3.81  1050.0  28.566914  77.436434       2.0        2.0      3.0   
4   6.20  1350.0  28.520732  77.356491       2.0        2.0      3.0   

   neworold  parking  Furnished_status  Lift  Landmarks  type_of_building  
0         1        0               0.0     1          0                 0  
1         1        0               1.0     1          0                 0  
2         1        1               0.0     0          0                 0  
3         1        1               0.0     1          1                 0  
4         0        1               0.0     1          0                 0

In [28]:
sns.set_style("whitegrid")
def map_func(data):
    map_data=data[['latitude','longitude','price']]
    city_map = folium.Map(location=[data.latitude.mean(),data.longitude.mean()], zoom_start=9.5, tiles='openstreetmap')
    mc = MarkerCluster()
    for idx, row in map_data.iterrows():
        popup = """
        Price : <b>%s</b><br>
        """ % ( row['price'])
        mc.add_child(folium.Marker([row['latitude'], row['longitude']],tooltip=popup))
        city_map.add_child(mc)
    return city_map
map_func(delhi)

## References
8. 
9. https://www.kaggle.com/code/goelyash/edta-and-house-price-prediction-r2-score-0-9337
10. https://python-visualization.github.io/folium/latest/user_guide/plugins/marker_cluster.html
11. 